<a href="https://colab.research.google.com/github/v-grand/Collector/blob/main/Crypto_ETL.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Instal

In [1]:
!pip install ta
!pip install mplfinance

  Preparing metadata (setup.py) ... done
  Created wheel for ta: filename=ta-0.11.0-py3-none-any.whl size=29412 sha256=2c24619b3fa125c627d045fb47e8a01728de26097686f7353b36ec8694016085
  Stored in directory: /root/.cache/pip/wheels/a1/d7/29/7781cc5eb9a3659d032d7d15bdd0f49d07d2b24fec29f44bc4
Successfully built ta
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.0/75.0 kB 1.9 MB/s eta 0:00:00


### Import

In [2]:

'''
%pip install prophet

'''
import requests
import urllib

import pandas as pd

import matplotlib.pyplot as plt
import matplotlib.dates as mdates
import numpy as np

import pandas as pd
from prophet import Prophet

from datetime import datetime, timedelta
import numpy as np
from pandas import DataFrame
import pandas as pd


from sklearn.preprocessing import MinMaxScaler
import ta
from typing import Tuple
import yfinance as yf

from sklearn.ensemble import RandomForestRegressor
import pandas as pd
from sklearn.model_selection import train_test_split
import joblib
from sklearn.metrics import mean_squared_error


from google.colab import drive
#from tensorflow.keras.models import load_model

from prophet import Prophet

# Подключение Google Drive
drive.mount('/content/drive')

Mounted at /content/drive


# Function

In [3]:
def prep_data(drop_na:bool = True, ticker='BTC-USD', period='60d', interval_='5m') -> DataFrame:

    N_pred=3

    data = yf.download(ticker, period=period, interval=interval_)


    data.drop(columns=['Adj Close','Volume'], inplace=True)

    data['NextOpen'] = data['Open'].shift(-1)
    data['NextHigh'] = data['High'].shift(-1)
    data['NextLow'] = data['Low'].shift(-1)
    data['NextClose'] = data['Close'].shift(-1)


    for i in range(1, N_pred):
      data[f'PrevOpen_bar{i}'] = data['Open'].shift(i)
      data[f'PrevHigh_bar{i}'] = data['High'].shift(i)
      data[f'PrevLow_bar{i}'] = data['Low'].shift(i)
      data[f'PrevClose_bar{i}'] = data['Close'].shift(i)

    data = data.iloc[N_pred:]


    # Drop NaN values
    if(drop_na):
        data.dropna(inplace=True)

    data.reset_index(inplace=True)

    if data.empty:
      print(f'No data found for {ticker}')
      return None
    else:

      if 'Date' in data.columns:
        last_date_value= data['Date'].iloc[-1]
        first_data_value=data['Date'].iloc[0]
        print(f'   {ticker} load at {first_data_value} to {last_date_value} interval {interval_}')

      elif 'Datetime' in data.columns:
        last_date_value= data['Datetime'].iloc[-1]
        first_data_value=data['Datetime'].iloc[0]
        print(f'   {ticker} load at {first_data_value} to {last_date_value} interval {interval_}')

    data.rename(columns=lambda x: f'{x}_{interval_}', inplace=True)

    return data


In [4]:
def scale_data(data:DataFrame, columns_x, columns_y) -> Tuple[MinMaxScaler, np.ndarray, np.ndarray]:

    # Prepare target variable
    y = data[columns_y].values
    X = data [columns_x]

    # Scale features
    scaler = MinMaxScaler(feature_range=(0, 1))
    X_scaled = scaler.fit_transform(X)
    y_scaled = scaler.fit_transform(y.reshape(-1, 1)).reshape(-1)

    return scaler, X_scaled, y_scaled

# EXTRACT

In [299]:
import yfinance as yf
import pandas as pd
import os

def extract_yf_data(ticker, periods, intervals):
    """
    Загружает данные для всех указанных интервалов и возвращает их в виде словаря.

    :param ticker: Символ тикера, например, 'BTC-USD'.
    :param periods: Период загрузки данных, например, '10y', 'max'.
    :param intervals: Список интервалов для загрузки данных, например, ['1m', '5m', '1d'].
    :return: Словарь с данными для каждого интервала.
    """
    datasets = {}

    for interval in intervals:
        try:
            print(f"Загрузка данных для интервала {interval}...")
            data = yf.download(tickers=ticker, period=periods, interval=interval)
            if data.empty:
                #print(f"Нет данных для интервала {interval}. Пропускаем.")
                continue
            else:
              # Добавляем столбец с интервалом для удобства
              #data['interval'] = interval

              # Сохраняем данные в словарь
              datasets[interval] = data
              print(f'{interval} ___ {datasets[interval].shape}')
              #print(datasets[interval].info())

        except Exception as e:
          pass
            #print(f"Ошибка при загрузке данных для интервала {interval}: {e}")

    print("Загрузка завершена.")
    return datasets




In [300]:
# Пример использования
ticker_ = 'BTC-USD'
period_ = 'max'
#intervals_ = ['1m', '2m', '5m', '15m', '30m', '60m', '90m', '1h', '1d', '5d', '1wk', '1mo', '3mo']
intervals_ = ['1m','5m', '15m', '30m', '60m', '90m', '1h', '1d', '5d', '1wk', '1mo', '3mo']



# Загрузка данных
datasets = extract_yf_data (ticker_, period_, intervals_)

Загрузка данных для интервала 1m...


[*********************100%***********************]  1 of 1 completed


1m ___ (7778, 5)
Загрузка данных для интервала 5m...


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed


5m ___ (17257, 5)
Загрузка данных для интервала 15m...
15m ___ (5754, 5)
Загрузка данных для интервала 30m...


...

60m ___ (17436, 5)
Загрузка данных для интервала 90m...
90m ___ (961, 5)
Загрузка данных для интервала 1h...


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed


1h ___ (17436, 5)
Загрузка данных для интервала 1d...
1d ___ (3783, 5)
Загрузка данных для интервала 5d...


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed

5d ___ (757, 5)
Загрузка данных для интервала 1wk...
1wk ___ (541, 5)
Загрузка данных для интервала 1mo...
1mo ___ (124, 5)
Загрузка данных для интервала 3mo...
3mo ___ (43, 5)
Загрузка завершена.


In [301]:
for dataset in datasets:
  print(dataset)
print(datasets[dataset].head())

1m
5m
15m
30m
60m
90m
1h
1d
5d
1wk
1mo
3mo
Price            Close        High         Low        Open      Volume
Ticker         BTC-USD     BTC-USD     BTC-USD     BTC-USD     BTC-USD
Date                                                                  
2014-09-01  378.046997  457.092987  289.295990  387.427002  1562727810
2014-12-01  254.263000  384.037994  171.509995  378.248993  2363432922
2015-03-01  230.190002  300.044006  214.873993  254.283005  2199559600
2015-06-01  230.056000  314.394012  199.567001  230.233002  2534864700
2015-09-01  377.321014  495.562012  225.117004  230.255997  3734526796


In [302]:
print(datasets[dataset].head())

Price            Close        High         Low        Open      Volume
Ticker         BTC-USD     BTC-USD     BTC-USD     BTC-USD     BTC-USD
Date                                                                  
2014-09-01  378.046997  457.092987  289.295990  387.427002  1562727810
2014-12-01  254.263000  384.037994  171.509995  378.248993  2363432922
2015-03-01  230.190002  300.044006  214.873993  254.283005  2199559600
2015-06-01  230.056000  314.394012  199.567001  230.233002  2534864700
2015-09-01  377.321014  495.562012  225.117004  230.255997  3734526796


In [303]:
print(datasets['1m'].info())

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 7778 entries, 2025-01-17 11:51:00+00:00 to 2025-01-24 11:47:00+00:00
Data columns (total 5 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   (Close, BTC-USD)   7778 non-null   float64
 1   (High, BTC-USD)    7778 non-null   float64
 2   (Low, BTC-USD)     7778 non-null   float64
 3   (Open, BTC-USD)    7778 non-null   float64
 4   (Volume, BTC-USD)  7778 non-null   int64  
dtypes: float64(4), int64(1)
memory usage: 364.6 KB
None


# TRANSFORM

In [304]:
prepared_datasets = {}  # Словарь для хранения подготовленных данных

## Rename

In [306]:
def process_dataframe(df, ticker_):
    # Сбрасываем индекс без добавления его в качестве нового столбца
    df.reset_index(inplace=True, drop=False)

    # Упрощаем MultiIndex, объединяя его уровни в строковые названия столбцов
    if isinstance(df.columns, pd.MultiIndex):
        df.columns = ['_'.join(filter(None, col)) if isinstance(col, tuple) else col for col in df.columns]

    # Попытка определить название временного столбца
    possible_time_columns = ['Datetime', 'Datet', 'index']  # Добавьте любые возможные варианты
    time_column = None
    for col in possible_time_columns:
        if col in df.columns:
            time_column = col
            df.rename(columns={time_column: 'D'}, inplace=True)

    if not time_column:
        raise ValueError("Не найден временной столбец ('Datetime', 'Date', или 'index') в данных.")

    # Переименовываем временной столбец в 'D'


    # Формируем словарь для переименования столбцов
    rename_dict = {
        f'Close_{ticker_}': 'C',
        f'High_{ticker_}': 'H',
        f'Low_{ticker_}': 'L',
        f'Open_{ticker_}': 'O',
        f'Volume_{ticker_}': 'V'
    }

    # Переименовываем столбцы
    df.rename(columns=rename_dict, inplace=True)

    return df


# Пример использования
prepared_datasets = {}  # Словарь для хранения обработанных наборов данных

for interval, dataset in datasets.items():
    print(f"Обработка {ticker_} данных для интервала {interval}...")

    try:
        prepared_data = process_dataframe(dataset, ticker_)
        prepared_datasets[interval] = prepared_data
    except ValueError as e:
        print(f"Ошибка при обработке интервала {interval}: {e}")


Обработка BTC-USD данных для интервала 1m...
Обработка BTC-USD данных для интервала 5m...
Обработка BTC-USD данных для интервала 15m...
Обработка BTC-USD данных для интервала 30m...
Обработка BTC-USD данных для интервала 60m...
Обработка BTC-USD данных для интервала 90m...
Обработка BTC-USD данных для интервала 1h...
Обработка BTC-USD данных для интервала 1d...
Обработка BTC-USD данных для интервала 5d...
Обработка BTC-USD данных для интервала 1wk...
Обработка BTC-USD данных для интервала 1mo...
Обработка BTC-USD данных для интервала 3mo...


In [311]:
prepared_datasets['1m'].head()

D                         D              C              H              L  \
0  0 2025-01-17 11:51:00+00:00  102267.890625  102267.890625  102267.890625   
1  1 2025-01-17 11:53:00+00:00  102266.414062  102266.414062  102266.414062   
2  2 2025-01-17 11:55:00+00:00  102241.007812  102241.007812  102241.007812   
3  3 2025-01-17 11:58:00+00:00  102239.625000  102239.625000  102239.625000   
4  4 2025-01-17 11:59:00+00:00  102235.335938  102235.335938  102235.335938   

               O  V  
0  102267.890625  0  
1  102266.414062  0  
2  102241.007812  0  
3  102239.625000  0  
4  102235.335938  0

## Log_Close

In [312]:
import numpy as np

def log_prices(df):
    """
    Логарифмирует столбец 'C' (цены закрытия) в переданном DataFrame.

    Аргументы:
    - df: pandas DataFrame, который должен содержать столбец 'C'.

    Возвращает:
    - DataFrame с добавленным столбцом 'Log_C', содержащим логарифм цен.
    """
    if 'C' not in df.columns:
        raise ValueError("Столбец 'C' (цены закрытия) отсутствует в данных.")

    # Добавляем логарифм цен в новый столбец 'Log_C'
    df['Log_C'] = np.log(df['C'])
    df['Log_O'] = np.log(df['O'])
    df['Log_H'] = np.log(df['H'])
    df['Log_L'] = np.log(df['L'])
    return df


# Пример использования:
for interval, dataset in prepared_datasets.items():
    print(f"Логарифмирование цен для интервала {interval}...")
    try:
        prepared_datasets[interval] = log_prices(dataset)
    except ValueError as e:
        print(f"Ошибка при обработке интервала {interval}: {e}")


Логарифмирование цен для интервала 1m...
Логарифмирование цен для интервала 5m...
Логарифмирование цен для интервала 15m...
Логарифмирование цен для интервала 30m...
Логарифмирование цен для интервала 60m...
Логарифмирование цен для интервала 90m...
Логарифмирование цен для интервала 1h...
Логарифмирование цен для интервала 1d...
Логарифмирование цен для интервала 5d...
Логарифмирование цен для интервала 1wk...
Логарифмирование цен для интервала 1mo...
Логарифмирование цен для интервала 3mo...


## calculate_ratios

In [313]:
def calculate_ratios(df):
    """
    Добавляет в DataFrame отношения High, Low, Open к Close и Log_C.

    Аргументы:
    - df: pandas DataFrame, который должен содержать столбцы 'H', 'L', 'O', 'C', 'Log_C'.

    Возвращает:
    - DataFrame с добавленными столбцами отношений:
      - 'H_to_C', 'L_to_C', 'O_to_C' — отношения High, Low, Open к Close.
      - 'H_to_Log_C', 'L_to_Log_C', 'O_to_Log_C' — отношения High, Low, Open к Log_C.
    """
    required_columns = ['H', 'L', 'O', 'C', 'Log_C']
    missing_columns = [col for col in required_columns if col not in df.columns]

    if missing_columns:
        raise ValueError(f"Отсутствуют необходимые столбцы: {', '.join(missing_columns)}")

    # Расчет отношений к Close
    df['H_to_C'] = df['H'] / df['C']
    df['L_to_C'] = df['L'] / df['C']
    df['O_to_C'] = df['O'] / df['C']

    # Расчет отношений к Log_C
    df['H_to_Log_C'] = df['H'] / df['Log_C']
    df['L_to_Log_C'] = df['L'] / df['Log_C']
    df['O_to_Log_C'] = df['O'] / df['Log_C']

    return df


# Пример использования:
for interval, dataset in prepared_datasets.items():
    print(f"Вычисление отношений для интервала {interval}...")
    try:
        prepared_datasets[interval] = calculate_ratios(dataset)
    except ValueError as e:
        print(f"Ошибка при обработке интервала {interval}: {e}")


Вычисление отношений для интервала 1m...
Вычисление отношений для интервала 5m...
Вычисление отношений для интервала 15m...
Вычисление отношений для интервала 30m...
Вычисление отношений для интервала 60m...
Вычисление отношений для интервала 90m...
Вычисление отношений для интервала 1h...
Вычисление отношений для интервала 1d...
Вычисление отношений для интервала 5d...
Вычисление отношений для интервала 1wk...
Вычисление отношений для интервала 1mo...
Вычисление отношений для интервала 3mo...


In [314]:
prepared_datasets['1d']

D       Date              C              H              L  \
0        0 2014-09-17     457.334015     468.174011     452.421997   
1        1 2014-09-18     424.440002     456.859985     413.104004   
2        2 2014-09-19     394.795990     427.834991     384.532013   
3        3 2014-09-20     408.903992     423.295990     389.882996   
4        4 2014-09-21     398.821014     412.425995     393.181000   
...    ...        ...            ...            ...            ...   
3778  3778 2025-01-20  102016.664062  109114.882812   99471.359375   
3779  3779 2025-01-21  106146.265625  107180.921875  100103.953125   
3780  3780 2025-01-22  103653.070312  106294.343750  103360.265625   
3781  3781 2025-01-23  103960.171875  106820.328125  101257.804688   
3782  3782 2025-01-24  105306.859375  105703.828125  102773.843750   

                  O             V      Log_C    H_to_C    L_to_C    O_to_C  \
0        465.864014      21056800   6.125414  1.023703  0.989259  1.018652   
1        456.859985      34483200   6.050771  1.076383  0.973292  1.076383   
2        424.102997      37919700   5.978369  1.083686  0.974002  1.074233   
3        394.673004      36863600   6.013480  1.035197  0.953483  0.965197   
4        408.084991      26580100   5.988513  1.034113  0.985858  1.023228   
...             ...           ...        ...       ...       ...       ...   
3778  101083.750000  126279678351  11.532891  1.069579  0.975050  0.990855   
3779  102052.578125   88733878242  11.572573  1.009747  0.943076  0.961434   
3780  106136.382812   53878181052  11.548805  1.025482  0.997175  1.023958   
3781  103657.671875  104104515428  11.551763  1.027512  0.974006  0.997090   
3782  103925.562500   95227404288  11.564634  1.003770  0.975946  0.986883   

       H_to_Log_C   L_to_Log_C   O_to_Log_C  
0       76.431407    73.859823    76.054290  
1       75.504429    68.272957    75.504429  
2       71.563830    64.320554    70.939580  
3       70.391182    64.834833    65.631378  
4       68.869520    65.655868    68.144631  
...           ...          ...          ...  
3778  9461.190480  8625.014793  8764.822804  
3779  9261.632588  8650.103192  8818.486226  
3780  9203.925960  8949.866931  9190.248273  
3781  9247.101660  8765.571406  8973.320401  
3782  9140.265884  8886.908587  8986.498316  

[3783 rows x 14 columns]

In [76]:
def prep_data(data, N_pred: int = 3, drop_na: bool = True, interval_: str = '5m') -> DataFrame:
    """
    Подготавливает данные, добавляя сдвинутые значения для предсказаний.

    :param data: Исходный датасет, предварительно загруженный.
    :param N_pred: Количество предыдущих шагов для создания признаков.
    :param drop_na: Удалять ли строки с NaN значениями.
    :param interval_: Интервал данных (используется для переименования колонок).
    :return: Подготовленный датасет.
    """
    data['NextOpen'] = data['Open'].shift(-1)
    data['NextHigh'] = data['High'].shift(-1)
    data['NextLow'] = data['Low'].shift(-1)
    data['NextClose'] = data['Close'].shift(-1)

    for i in range(1, N_pred):
        data[f'PrevOpen_bar{i}'] = data['Open'].shift(i)
        data[f'PrevHigh_bar{i}'] = data['High'].shift(i)
        data[f'PrevLow_bar{i}'] = data['Low'].shift(i)
        data[f'PrevClose_bar{i}'] = data['Close'].shift(i)

    data = data.iloc[N_pred:]

    # Drop NaN values
    if drop_na:
        data.dropna(inplace=True)

    data.reset_index(inplace=True)

    if 'Date' in data.columns:
        last_date_value = data['Date'].iloc[-1]
        first_data_value = data['Date'].iloc[0]
        print(f'   Data loaded from {first_data_value} to {last_date_value} interval {interval_}')

    elif 'Datetime' in data.columns:
        last_date_value = data['Datetime'].iloc[-1]
        first_data_value = data['Datetime'].iloc[0]
        print(f'   Data loaded from {first_data_value} to {last_date_value} interval {interval_}')

    data.rename(columns=lambda x: f'{x}_{interval_}', inplace=True)

    return data



In [79]:
#['1m','5m', '15m', '30m', '60m', '90m', '1h', '1d', '5d', '1wk', '1mo', '3mo']
# Пример использования с разными N_pred для каждого интервала
N_pred_dict = {
    '1m':1000,
    '5m':1000,
    '15m':1000,
    '30m':1000,
    '60m': 500,
    '90m': 500,
    '1h': 4,
    '1d': 2,
    '5d':100,
    '1wk':52,
    '3mo':16
}

prepared_datasets = {}  # Словарь для хранения подготовленных данных

for interval, dataset in datasets.items():
    print(f"Обработка данных для интервала {interval}...")
    N_pred = N_pred_dict.get(interval, 3)  # Получить N_pred для интервала, по умолчанию 3
    prepared_data = prep_data(dataset, N_pred=N_pred, drop_na=True, interval_=interval)
    prepared_datasets[interval] = prepared_data

Обработка данных для интервала 1m...


Выходные данные были обрезаны до нескольких последних строк (5000).
<ipython-input-76-8646dbca03db>:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevHigh_bar{i}'] = data['High'].shift(i)
<ipython-input-76-8646dbca03db>:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevLow_bar{i}'] = data['Low'].shift(i)
<ipython-input-76-8646dbca03db>:20: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all co

   Data loaded from 2025-01-18 11:06:00+00:00 to 2025-01-24 10:23:00+00:00 interval 1m
Обработка данных для интервала 5m...


Выходные данные были обрезаны до нескольких последних строк (5000).
<ipython-input-76-8646dbca03db>:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevLow_bar{i}'] = data['Low'].shift(i)
<ipython-input-76-8646dbca03db>:20: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevClose_bar{i}'] = data['Close'].shift(i)
<ipython-input-76-8646dbca03db>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all 

   Data loaded from 2024-11-28 21:45:00+00:00 to 2025-01-24 10:20:00+00:00 interval 5m
Обработка данных для интервала 15m...


...

<ipython-input-76-8646dbca03db>:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevHigh_bar{i}'] = data['High'].shift(i)
<ipython-input-76-8646dbca03db>:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevLow_bar{i}'] = data['Low'].shift(i)
<ipython-input-76-8646dbca03db>:20: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmente

   Data loaded from 2016-01-30 00:00:00 to 2025-01-17 00:00:00 interval 5d
Обработка данных для интервала 1wk...


<ipython-input-76-8646dbca03db>:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevHigh_bar{i}'] = data['High'].shift(i)
<ipython-input-76-8646dbca03db>:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevLow_bar{i}'] = data['Low'].shift(i)
<ipython-input-76-8646dbca03db>:20: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmente

   Data loaded from 2015-09-14 00:00:00 to 2025-01-13 00:00:00 interval 1wk
Обработка данных для интервала 1mo...
   Data loaded from 2015-01-01 00:00:00 to 2024-12-01 00:00:00 interval 1mo
Обработка данных для интервала 3mo...
   Data loaded from 2018-09-01 00:00:00 to 2024-12-01 00:00:00 interval 3mo


<ipython-input-76-8646dbca03db>:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data.dropna(inplace=True)
<ipython-input-76-8646dbca03db>:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data.rename(columns=lambda x: f'{x}_{interval_}', inplace=True)


In [87]:
prepared_datasets['1d'].head()

Price     Date_1d    Close_1d     High_1d      Low_1d     Open_1d  Volume_1d  \
Ticker        _1d  BTC-USD_1d  BTC-USD_1d  BTC-USD_1d  BTC-USD_1d BTC-USD_1d   
0      2014-09-19  394.795990  427.834991  384.532013  424.102997   37919700   
1      2014-09-20  408.903992  423.295990  389.882996  394.673004   36863600   
2      2014-09-21  398.821014  412.425995  393.181000  408.084991   26580100   
3      2014-09-22  402.152008  406.915985  397.130005  399.100006   24127600   
4      2014-09-23  435.790985  441.557007  396.196991  402.092010   45099500   

Price  interval_1d NextOpen_1d NextHigh_1d  NextLow_1d NextClose_1d  \
Ticker         _1d         _1d         _1d         _1d          _1d   
0               1d  394.673004  423.295990  389.882996   408.903992   
1               1d  408.084991  412.425995  393.181000   398.821014   
2               1d  399.100006  406.915985  397.130005   402.152008   
3               1d  402.092010  441.557007  396.196991   435.790985   
4               1d  435.751007  436.112000  421.131989   423.204987   

Price  PrevOpen_bar1_1d PrevHigh_bar1_1d PrevLow_bar1_1d PrevClose_bar1_1d  
Ticker              _1d              _1d             _1d               _1d  
0            456.859985       456.859985      413.104004        424.440002  
1            424.102997       427.834991      384.532013        394.795990  
2            394.673004       423.295990      389.882996        408.903992  
3            408.084991       412.425995      393.181000        398.821014  
4            399.100006       406.915985      397.130005        402.152008

In [309]:
for dataset in prepared_datasets:
  print(dataset)
  print(prepared_datasets[dataset].info())

1m
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7778 entries, 0 to 7777
Data columns (total 7 columns):
 #   Column  Non-Null Count  Dtype              
---  ------  --------------  -----              
 0   D       7778 non-null   int64              
 1   D       7778 non-null   datetime64[ns, UTC]
 2   C       7778 non-null   float64            
 3   H       7778 non-null   float64            
 4   L       7778 non-null   float64            
 5   O       7778 non-null   float64            
 6   V       7778 non-null   int64              
dtypes: datetime64[ns, UTC](1), float64(4), int64(2)
memory usage: 425.5 KB
None
5m
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17257 entries, 0 to 17256
Data columns (total 7 columns):
 #   Column  Non-Null Count  Dtype              
---  ------  --------------  -----              
 0   D       17257 non-null  int64              
 1   D       17257 non-null  datetime64[ns, UTC]
 2   C       17257 non-null  float64            
 3   H       

In [310]:
print(prepared_datasets[dataset].head())

   D       Date           C           H           L           O           V
0  0 2014-09-01  378.046997  457.092987  289.295990  387.427002  1562727810
1  1 2014-12-01  254.263000  384.037994  171.509995  378.248993  2363432922
2  2 2015-03-01  230.190002  300.044006  214.873993  254.283005  2199559600
3  3 2015-06-01  230.056000  314.394012  199.567001  230.233002  2534864700
4  4 2015-09-01  377.321014  495.562012  225.117004  230.255997  3734526796


In [70]:
from sklearn.ensemble import RandomForestRegressor
import pandas as pd
from sklearn.model_selection import train_test_split
import joblib
from sklearn.metrics import mean_squared_error

X_train, X_test, y_train, y_test = train_test_split(X_scaled, y_scaled, test_size=0.2, random_state=42)

model_name = "/content/drive/My Drive/High_random_forest.joblib"
    # Random Forest model
model_High = RandomForestRegressor(n_estimators=100, random_state=42)
model_High.fit(X_train, y_train)

    # Save the model to Google Drive
joblib.dump(model_High, model_name)

    # Predict the prices
predicted_prices = model_High.predict(X_test)

    # Evaluate
mse = mean_squared_error(y_test, predicted_prices)
print(f'Mean Squared Error: {mse}')
#feature_importance_high = model_High.feature_importances_
#feature_df_high = pd.DataFrame({'Feature': data_x.columns, 'Importance': feature_importance_high})

NameError: name 'X_scaled' is not defined

In [ ]:
# developer: Foundry Digital
# Copyright © 2023 Foundry Digital

# Import necessary modules to use for model creation - can be downloaded using pip
import joblib
import numpy as np
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Dropout

def create_and_save_base_model_lstm(scaler:MinMaxScaler, X_scaled:np.ndarray, y_scaled:np.ndarray) -> float:
    """
    Base model that can be created for predicting the S&P 500 close price

    The function creates a base model, given a scaler, inputs and outputs, and
    stores the model weights as a .h5 file in the mining_models/ folder. The model
    architecture and model name given now is a placeholder, can (and should)
    be changed by miners to build more robust models.

    Input:
        :param scaler: The scaler used to scale the inputs during model training process
        :type scaler: sklearn.preprocessing.MinMaxScaler

        :param X_scaled: The already scaled input data that will be used by the model to train and test
        :type X_scaled: np.ndarray

        :param y_scaled: The already scaled output data that will be used by the model to train and test
        :type y_scaled: np.ndarray

    Output:
        :returns: The MSE of the model on the test data
        :rtype: float
    """
    model_name = "mining_models/base_lstm"

    # Reshape input for LSTM
    X_scaled = X_scaled.reshape((X_scaled.shape[0], 1, X_scaled.shape[1]))

    # Split data into training and testing
    X_train, X_test, y_train, y_test = train_test_split(X_scaled, y_scaled, test_size=0.2, random_state=42)

    # LSTM model - all hyperparameters are baseline params - should be changed according to your required
    # architecture. LSTMs are also not the only way to do this, can be done using any algo deemed fit by
    # the creators of the miner.
    model = Sequential()
    model.add(LSTM(units=50, return_sequences=True, input_shape=(X_scaled.shape[1], X_scaled.shape[2])))
    model.add(Dropout(0.2))
    model.add(LSTM(units=50, return_sequences=False))
    model.add(Dropout(0.2))
    model.add(Dense(units=1))

    # Compile the model
    model.compile(optimizer='adam', loss='mean_squared_error')

    # Train the model
    model.fit(X_train, y_train, epochs=100, batch_size=32)
    model.save(f'{model_name}.h5')

    # Predict the prices - this is just for a local test, this prediction just allows
    # miners to assess the performance of their models on real data.
    predicted_prices = model.predict(X_test)

    # Rescale back to original range
    predicted_prices = scaler.inverse_transform(predicted_prices)
    y_test_rescaled = scaler.inverse_transform(y_test.reshape(-1, 1))

    # Evaluate
    mse = mean_squared_error(y_test_rescaled, predicted_prices)
    print(f'Mean Squared Error: {mse}')

    return mse

def create_and_save_base_model_regression(scaler:MinMaxScaler, X_scaled:np.ndarray, y_scaled:np.ndarray) -> float:
    """
    Base model that can be created for predicting the S&P 500 close price

    The function creates a base model, given a scaler, inputs and outputs, and
    stores the model weights as a .h5 file in the mining_models/ folder. The model
    architecture and model name given now is a placeholder, can (and should)
    be changed by miners to build more robust models.

    Input:
        :param scaler: The scaler used to scale the inputs during model training process
        :type scaler: sklearn.preprocessing.MinMaxScaler

        :param X_scaled: The already scaled input data that will be used by the model to train and test
        :type X_scaled: np.ndarray

        :param y_scaled: The already scaled output data that will be used by the model to train and test
        :type y_scaled: np.ndarray

    Output:
        :returns: The MSE of the model on the test data
        :rtype: float
    """
    model_name = "mining_models/base_linear_regression"

    # Split data into training and testing
    X_train, X_test, y_train, y_test = train_test_split(X_scaled, y_scaled, test_size=0.2, random_state=42)

    # LSTM model - all hyperparameters are baseline params - should be changed according to your required
    # architecture. LSTMs are also not the only way to do this, can be done using any algo deemed fit by
    # the creators of the miner.
    model = LinearRegression()
    model.fit(X_train, y_train)

    '''with h5py.File(f'{model_name}.h5', 'w') as hf:
        hf.create_dataset('coefficients', data=model.coef_)
        hf.create_dataset('intercept', data=model.intercept_)'''
    joblib.dump(model, f"{model_name}.joblib")

    # Predict the prices - this is just for a local test, this prediction just allows
    # miners to assess the performance of their models on real data.
    predicted_prices = model.predict(X_test)

    # Rescale back to original range
    predicted_prices = scaler.inverse_transform(predicted_prices.reshape(-1, 1))
    y_test_rescaled = scaler.inverse_transform(y_test.reshape(-1, 1))

    # Evaluate
    mse = mean_squared_error(y_test_rescaled, predicted_prices)
    print(f'Mean Squared Error: {mse}')

    return mse

# Spread

In [ ]:
interval_='1d'
period_='300d'

ticker_2='XRP-USD'
ticker_1='ATOM-USD'
K_1=1
K_2=20

data_1 = prep_data(drop_na=True, ticker=ticker_1, period=period_, interval_=interval_)
#print(data_1.shape)

data_2 = prep_data(drop_na=True, ticker=ticker_2, period=period_, interval_=interval_)
#print(data_2.shape)


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed

   ATOM-USD load at 2019-03-17 00:00:00 to 2025-01-02 00:00:00 interval 1d
   XRP-USD load at 2017-11-12 00:00:00 to 2025-01-02 00:00:00 interval 1d


In [ ]:
# Объединяем датасеты по столбцу Datetime
combined_df = pd.merge(data_1, data_2, on='Datetime_1h', how='inner')

combined_df['Close']=K_1*combined_df['Close_1h_x']-K_2*combined_df['Close_1h_y']
#combined_df.info()

TypeError: Can only merge Series or DataFrame objects, a <class 'NoneType'> was passed

In [ ]:
from prophet import Prophet

dp_ds = combined_df[['Datetime_1h', 'Close']].copy()
dp_ds['Datetime_1h'] = dp_ds['Datetime_1h'].dt.tz_localize(None)

# Подготовка данных для Prophet
dp_ds = dp_ds.rename(columns={'Datetime_1h': 'ds', 'Close': 'y'})


model = Prophet(
    growth='linear',
    changepoint_range=0.8,
    seasonality_mode='additive',
    seasonality_prior_scale=10.0,
    holidays_prior_scale=10.0,
    changepoint_prior_scale=0.05,
    interval_width=0.8,
    uncertainty_samples=10
)
# Продолжаем обучение и прогнозирование

model.fit(dp_ds)

# Создание будущего DataFrame для прогнозов
future = model.make_future_dataframe(periods=30)  # Прогноз на 30 дней вперед

# Получение прогнозов
forecast = model.predict(future)



In [ ]:
# Построение графика прогнозов
fig = model.plot( forecast.iloc[-100:])
plt.xlabel(f'Date')
plt.ylabel('Quote')
plt.title(f'{ticker_1}x{K_1} and {ticker_2}x{K_2}')
plt.show()